In [0]:
# import libraries
import pyspark.sql.functions as F
from pyspark.sql.types import *
from datetime import datetime
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from pyspark.ml.linalg import DenseVector, SparseVector, Vectors
from pyspark.ml.feature import VectorAssembler, StandardScaler

from pyspark.ml import Pipeline
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

from pyspark.ml.classification import RandomForestClassifier, DecisionTreeClassifier, LogisticRegression, GBTClassifier 
from pyspark.ml.evaluation import MulticlassClassificationEvaluator, BinaryClassificationEvaluator
from sparkdl.xgboost import XgboostClassifier

In [0]:
# set up storage
blob_container = "container1" # The name of your container created in https://portal.azure.com
storage_account = "w261sec6group3" # The name of your Storage account created in https://portal.azure.com
secret_scope = "w261sec6group3_scope" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "w261sec6group3_key" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

spark.conf.set(
  f"fs.azure.sas.{blob_container}.{storage_account}.blob.core.windows.net",
  dbutils.secrets.get(scope = secret_scope, key = secret_key)
)

### Load Data

In [0]:
# read preprocessed dataset from blob storage
df_final = spark.read.parquet(f"{blob_url}/final_vectorized_new")

In [0]:
df_final.display()

quarter month day_of_month day_of_week fl_date op_unique_carrier op_carrier_airline_id op_carrier tail_num op_carrier_fl_num origin_airport_id origin_airport_seq_id origin_city_market_id origin origin_city_name origin_state_abr origin_state_fips origin_state_nm origin_wac dest_airport_id dest_airport_seq_id dest_city_market_id dest dest_city_name dest_state_abr dest_state_fips dest_state_nm dest_wac crs_dep_time dep_time dep_delay dep_delay_new dep_del15 dep_delay_group dep_time_blk taxi_out wheels_off wheels_on taxi_in crs_arr_time arr_time arr_delay arr_delay_new arr_del15 arr_delay_group arr_time_blk cancelled diverted crs_elapsed_time actual_elapsed_time air_time flights distance distance_group div_airport_landings year IATA station_id name icao lat lon altitude station_lon station_lat timezone type crs_dep_hour flight_hour flight_time flight_time_utc flight_time_utc_hour flight_time_utc_year flight_time_utc_month flight_time_utc_date is_holiday weather_station weather_station_name metar_hour avg_hourly_dew_point_temp avg_hourly_dry_bulb_temp avg_hourly_relative_humidity avg_hourly_station_pressure avg_hourly_visibility avg_hourly_wind_direction avg_hourly_wind_speed avg_hourly_precipitation_ordinal pagerank avg_hourly_dew_point_temp_lag6 avg_hourly_dry_bulb_temp_lag6 avg_hourly_relative_humidity_lag6 avg_hourly_station_pressure_lag6 avg_hourly_visibility_lag6 avg_hourly_wind_direction_lag6 avg_hourly_wind_speed_lag6 avg_hourly_precipitation_ordinal_lag6 avg_hourly_dew_point_temp_lag12 avg_hourly_dry_bulb_temp_lag12 avg_hourly_relative_humidity_lag12 avg_hourly_station_pressure_lag12 avg_hourly_visibility_lag12 avg_hourly_wind_direction_lag12 avg_hourly_wind_speed_lag12 avg_hourly_precipitation_ordinal_lag12 arr_del15_lag1 origin_lag1 frequent_delay total_flights quarterIndex quarterclassVec day_of_weekIndex day_of_weekclassVec op_unique_carrierIndex op_unique_carrierclassVec tail_numIndex tail_numclassVec originIndex originclassVec origin_state_abrIndex origin_state_abrclassVec destIndex destclassVec dest_state_abrIndex dest_state_abrclassVec crs_dep_hourIndex crs_dep_hourclassVec flight_time_utc_hourIndex flight_time_utc_hourclassVec flight_time_utc_yearIndex flight_time_utc_yearclassVec flight_time_utc_monthIndex flight_time_utc_monthclassVec avg_hourly_wind_directionIndex avg_hourly_wind_directionclassVec avg_hourly_wind_direction_lag6Index avg_hourly_wind_direction_lag6classVec avg_hourly_wind_direction_lag12Index avg_hourly_wind_direction_lag12classVec arr_del15_lag1Index arr_del15_lag1classVec origin_lag1Index origin_lag1classVec is_holidayIndex is_holidayclassVec frequent_delayIndex frequent_delayclassVec features 1 1 30 5 2015-01-30 WN 19393 WN N218WN 2428 10423 1042302 30423 AUS Austin, TX TX 48 Texas 74 11259 1125903 30194 DAL Dallas, TX TX 48 Texas 74 2145 2141 -4.0 0.0 0.0 -1 2100-2159 15.0 2156 2231 4.0 2240 2235 -5.0 0.0 0.0 -1 2200-2259 0.0 0.0 55.0 54.0 35.0 1.0 189.0 1 0 2015 AUS 72254013904 Austin Bergstrom International Airport KAUS 30.194499969482422 -97.6698989868164 542 -97.68 30.183 America/Chicago large_airport 21.0 2145 2015-01-30T21:45:00.000+0000 2015-01-31T03:45:00.000+0000 3 2015 1 31 0 72254013904 AUSTIN BERGSTROM INTERNATIONAL AIRPORT, TX US 2015-01-31T00:00:00.000+0000 40.0 50.0 68.0 29.709999084472656 10.0 70.0 5.0 0.0 5.0 39.0 51.0 64.0 29.75 10.0 40.0 6.0 0.0 40.0 57.0 53.0 29.760000228881836 10.0 40.0 9.0 0.0 0.0 ATL 2 446585 1.0 Map(vectorType -> sparse, length -> 3, indices -> List(1), values -> List(1.0)) 0.0 Map(vectorType -> sparse, length -> 6, indices -> List(0), values -> List(1.0)) 0.0 Map(vectorType -> sparse, length -> 19, indices -> List(0), values -> List(1.0)) 120.0 Map(vectorType -> sparse, length -> 8399, indices -> List(120), values -> List(1.0)) 32.0 Map(vectorType -> sparse, length -> 375, indices -> List(32), values -> List(1.0)) 1.0 Map(vectorType -> sparse, length -> 50, indices -> List(1), values -> List(1.0)) 27.0 Map(vectorType -> sparse, length -> 383, indices 

In [0]:
# keep only the necessary columns for training and testing (year and quarter features are used for CV)
df_model = df_final['features', 'dep_del15', 'flight_time_utc_year', 'quarter']
df_model = df_model.withColumnRenamed("dep_del15", "label")
df_model = df_model.withColumnRenamed("flight_time_utc_year", "year")

# split the dataset into train and test
df_train = df_model.filter(F.col("year") < 2021)
df_test = df_model.filter(F.col("year") == 2021)

In [0]:
df_train.display()

features label year quarter Map(vectorType -> sparse, length -> 13532, indices -> List(1, 3, 9, 148, 8459, 8803, 8879, 9236, 9302, 9327, 9336, 9342, 9387, 10615, 11902, 13129, 13130, 13505, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13516, 13518, 13519, 13520, 13521, 13522, 13523, 13525, 13526, 13527, 13528, 13529, 13530), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 55.0, 5.0, 446585.0, 40.0, 50.0, 68.0, 29.709999084472656, 10.0, 5.0, 39.0, 51.0, 64.0, 29.75, 10.0, 6.0, 40.0, 57.0, 53.0, 29.760000228881836, 10.0, 9.0)) 0.0 2015 1 Map(vectorType -> sparse, length -> 13532, indices -> List(1, 8, 12, 865, 8430, 8808, 8976, 9258, 9296, 9324, 9336, 9342, 9383, 10609, 11869, 13129, 13208, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13516, 13518, 13519, 13520, 13521, 13522, 13523, 13525, 13526, 13527, 13528, 13529), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 173.0, 5.0, 446585.0, 22.0, 29.0, 75.0, 24.709999084472656, 10.0, 5.0, 23.0, 28.0, 81.0, 24.700000762939453, 10.0, 6.0, 15.0, 42.0, 33.0, 24.649999618530273, 10.0)) 0.0 2015 1 Map(vectorType -> sparse, length -> 13532, indices -> List(1, 9, 202, 8438, 8814, 8927, 9247, 9299, 9317, 9336, 9342, 9358, 10600, 11876, 13225, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13516, 13518, 13519, 13520, 13521, 13522, 13523, 13525, 13526, 13527, 13528, 13529, 13530), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 145.0, 5.0, 446585.0, 16.0, 44.0, 32.0, 27.93000030517578, 10.0, 7.0, 15.0, 48.0, 27.0, 27.860000610351562, 10.0, 3.0, 13.0, 47.0, 25.0, 27.8700008392334, 10.0, 3.0)) 0.0 2015 1 Map(vectorType -> sparse, length -> 13532, indices -> List(1, 3, 13, 1692, 8484, 8810, 8853, 9239, 9295, 9315, 9336, 9342, 9363, 10604, 11875, 13129, 13131, 13505, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13516, 13518, 13519, 13520, 13521, 13522, 13523, 13525, 13526, 13527, 13528, 13529, 13530), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 134.0, 5.0, 446585.0, 20.0, 44.0, 38.0, 29.850000381469727, 10.0, 15.0, 27.0, 43.0, 53.0, 29.829999923706055, 10.0, 14.0, 25.0, 41.0, 53.0, 29.739999771118164, 10.0, 5.0)) 0.0 2015 1 Map(vectorType -> sparse, length -> 13532, indices -> List(1, 8, 9, 1377, 8496, 8814, 8859, 9246, 9288, 9313, 9336, 9342, 9351, 10582, 11869, 13129, 13155, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13518, 13519, 13520, 13521, 13522, 13525, 13526, 13527, 13528, 13529), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 85.0, 5.0, 446585.0, 25.0, 49.0, 39.0, 25.68000030517578, 10.0, 28.0, 38.0, 68.0, 25.75, 10.0, 26.0, 31.0, 82.0, 25.719999313354492, 10.0)) 0.0 2015 1 Map(vectorType -> sparse, length -> 13532, indices -> List(1, 4, 9, 530, 8496, 8814, 8859, 9246, 9300, 9327, 9336, 9342, 9351, 10610, 11888, 13129, 13137, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13518, 13519, 13520, 13521, 13522, 13523, 13525, 13526, 13527, 13528, 13529, 13530), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 70.0, 5.0, 446585.0, 27.0, 37.0, 67.0, 25.719999313354492, 10.0, 27.0, 40.0, 60.0, 25.760000228881836, 10.0, 3.0, 25.0, 48.0, 41.0, 25.770000457763672, 10.0, 3.0)) 0.0 2015 1 Map(vectorType -> sparse, length -> 13532, indices -> List(1, 3, 9, 213, 8451, 8802, 8890, 9235, 9297, 9310, 9336, 9342, 9351, 10589, 11869, 13129, 13176, 13505, 13508, 13509, 13510, 13511, 13512, 13513, 13514, 13515, 13518, 13519, 13520, 13521, 13522, 13523, 13525, 13526, 13527, 13528, 13529), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 90.0, 5.0, 446585.0, 52.0, 62.0, 70.0, 29.8700008392334, 10.0, 49.0, 63.0, 60.0, 29.850000381469727, 10.0, 5.0, 55.0, 62.0, 78.0, 29.93000030517578, 1

### UnderSampling

In [0]:
sample_ratio  = (df_train.filter(df_train.label == 1).count())/(df_train.filter(df_train.label == 0).count())

sample_df_train = df_train.filter(df_train.label == 1)
for i in [2015, 2016, 2017, 2018, 2019, 2020]:
  sample_0_df = df_train.filter((df_train.label == 0) &(df_train.year == i)).sample(False, sample_ratio, seed= 2022)
  sample_df_train = sample_df_train.unionAll(sample_0_df)

In [0]:
sample_df_train.write.mode('overwrite').parquet(f"{blob_url}/final_train_dataset")

In [0]:
df_test.write.mode('overwrite').parquet(f"{blob_url}/final_test_2021_dataset")

In [0]:
sample_df_train = spark.read.parquet(f"{blob_url}/final_train_dataset")
sample_df_train.display()

In [0]:
df_test = spark.read.parquet(f"{blob_url}/final_test_2021_dataset")
df_test.display()

### Fit in Custom CV

In [0]:
# import custom cv module
spark.sparkContext.addPyFile("dbfs:/custom_cv.py")
from custom_cv import CustomCrossValidator


# set up grid search: estimator, set of params, and evaluator
lr = LogisticRegression(featuresCol='features', labelCol='label', maxIter=10)
rf = RandomForestClassifier(labelCol="label", featuresCol="features")
xgb = XgboostClassifier(num_workers=3, featuresCol="features", labelCol="label", missing=0.0, max_depth=2, n_estimators= 100, numEarlyStoppingRounds=10)

grid_rf = ParamGridBuilder()\
            .addGrid(rf.maxDepth, [5])\
            .addGrid(rf.numTrees, [20])\
            .build()

# grid search
grid_xgb = ParamGridBuilder()\
  .addGrid(xgb.max_depth, [5])\
  .addGrid(xgb.n_estimators, [100])\
  .build()

# lr grid search
grid_lr = ParamGridBuilder()\
      .addGrid(lr.standardization,[True, False])\
      .build()



evaluator = BinaryClassificationEvaluator()

In [0]:
def cal_metrics(df):
  tp = df[(df.label == 1) & (df.prediction == 1)].count()
  tn = df[(df.label == 0) & (df.prediction == 0)].count()
  fp = df[(df.label == 0) & (df.prediction == 1)].count()
  fn = df[(df.label == 1) & (df.prediction == 0)].count()

  precision = tp / (tp + fp)
  recall = tp / (tp + fn)
  
  accuracy = (tp+tn)/(tp+tn+fp+fn)

  F_beta = (1.25 * precision * recall) / (0.25 * precision + recall)
  print("Test F0.5 Score: ", F_beta)
  print("Test Precision Score: ", precision)
  print("Test Recall Score: ", recall)
  print("Test Accuracy Score: ", accuracy)

In [0]:
d = {}

d['df1'] = sample_df_train.filter((sample_df_train.year == 2015) | ((sample_df_train.year == 2016) & (sample_df_train.quarter == 1)))\
                   .withColumn('cv', F.when(sample_df_train.year == 2015, 'train')
                                         .otherwise('test'))

d['df2'] = sample_df_train.filter((sample_df_train.year == 2016) | ((sample_df_train.year == 2017) & (sample_df_train.quarter == 1)))\
                   .withColumn('cv', F.when(sample_df_train.year == 2016, 'train')
                                         .otherwise('test'))

d['df3'] = sample_df_train.filter((sample_df_train.year == 2017) | ((sample_df_train.year == 2018) & (sample_df_train.quarter == 1)))\
                   .withColumn('cv', F.when(sample_df_train.year == 2017, 'train')
                                         .otherwise('test'))

d['df4'] = sample_df_train.filter((sample_df_train.year == 2018) | ((sample_df_train.year == 2019) & (sample_df_train.quarter == 1)))\
                   .withColumn('cv', F.when(sample_df_train.year == 2018, 'train')
                                         .otherwise('test'))

d['df5'] = sample_df_train.filter((sample_df_train.year == 2019) | ((sample_df_train.year == 2020) & (sample_df_train.quarter == 1)))\
                   .withColumn('cv', F.when(sample_df_train.year == 2019, 'train')
                                         .otherwise('test'))

In [0]:
for i in d:
  d[i] = d[i].withColumn("cv_flag", F.when(d[i].cv == "train",False )
                                 .when(d[i].cv == "test",True)
                                 )

In [0]:
# Check balance
d['df1'].groupby('year','cv').count().orderBy('year').show()
d['df2'].groupby('year','cv').count().orderBy('year').show()
d['df3'].groupby('year','cv').count().orderBy('year').show()
d['df4'].groupby('year','cv').count().orderBy('year').show()
d['df5'].groupby('year','cv').count().orderBy('year').show()


+----+-----+-------+
year| cv| count|
+----+-----+-------+
2015|train|1743803|
2016| test| 393321|
+----+-----+-------+

+----+-----+-------+
year| cv| count|
+----+-----+-------+
2016|train|1623363|
2017| test| 411277|
+----+-----+-------+

+----+-----+-------+
year| cv| count|
+----+-----+-------+
2017|train|1674740|
2018| test| 509103|
+----+-----+-------+

+----+-----+-------+
year| cv| count|
+----+-----+-------+
2018|train|2144958|
2019| test| 536905|
+----+-----+-------+

+----+-----+-------+
year| cv| count|
+----+-----+-------+
2019|train|2172390|
2020| test| 469816|
+----+-----+-------+

#### Logistic Regression and Decision Tree

https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/849916349911411/command/849916349917740

#### Random Forest

In [0]:
# run cross validation
cv_rf = CustomCrossValidator(estimator=rf, evaluator=evaluator, estimatorParamMaps=grid_rf, splitWord = ('train', 'test'), cvCol = 'cv', parallelism=10)

cvModel_rf = cv_rf.fit(d)

fold 1 start...
fold 1 end
fold 2 start...
fold 2 end
fold 3 start...
fold 3 end
fold 4 start...
fold 4 end
fold 5 start...
fold 5 end
Best Model: {Param(parent='RandomForestClassifier_71b0d2d32439', name='maxDepth', doc='Maximum depth of the tree. (>= 0) E.g., depth 0 means 1 leaf node; depth 1 means 1 internal node + 2 leaf nodes. Must be in range [0, 30].'): 5, Param(parent='RandomForestClassifier_71b0d2d32439', name='numTrees', doc='Number of trees to train (>= 1).'): 20} Detailed Score [0.7622007749830799, 0.7607226540824477, 0.776189093629226, 0.7654706865588268, 0.7620604528410602] Avg Score 0.7653287324189281

In [0]:
fold 1 start...
fold 1 end
fold 2 start...
fold 2 end
fold 3 start...
fold 3 end
fold 4 start...
fold 4 end
fold 5 start...
fold 5 end
Best Model:  {Param(parent='RandomForestClassifier_0f3d09ee9160', name='maxDepth', doc='Maximum depth of the tree. (>= 0) E.g., depth 0 means 1 leaf node; depth 1 means 1 internal node + 2 leaf nodes. Must be in range [0, 30].'): 10, Param(parent='RandomForestClassifier_0f3d09ee9160', name='numTrees', doc='Number of trees to train (>= 1).'): 15} Detailed Score [0.6546401388505421, 0.7393021933110175, 0.6811848878077641, 0.7594602698603996, 0.7572991909482532] Avg Score 0.7183773361555954

In [0]:
rf3 = RandomForestClassifier(labelCol="label", featuresCol="features", maxDepth = 10, numTrees = 15)
cvModel_rf3 = rf3.fit(sample_df_train)
prediction3 = cvModel_rf3.transform(df_test)
cal_metrics(prediction3['label', 'prediction'])

Test F0.5 Score: 0.47782187435223894
Test Precision Score: 0.46292945258099716
Test Recall Score: 0.5483884057030103
Test Accuracy Score: 0.8115287514770781

#### XGboost

https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/849916349916003/command/849916349916004

SMOTE

In [0]:
import random
import numpy as np
from pyspark.sql import Row
from sklearn import neighbors
from pyspark.ml.feature import VectorAssembler


def SmoteSampling(vectorized, k = 5, minorityClass = 1, majorityClass = 0, percentageOver = 200, percentageUnder = 100):
  
    dataInput_min = vectorized[vectorized['label'] == minorityClass]
    dataInput_maj = vectorized[vectorized['label'] == majorityClass]
    feature = dataInput_min.select('features')
    feature = feature.rdd
    feature = feature.map(lambda x: x[0])
    feature = feature.collect()
    feature = np.asarray(feature)
    nbrs = neighbors.NearestNeighbors(n_neighbors=k, algorithm='auto').fit(feature)
    neighbours =  nbrs.kneighbors(feature)
    gap = neighbours[0]
    neighbours = neighbours[1]
    min_rdd = dataInput_min.drop('label').rdd
    pos_rddArray = min_rdd.map(lambda x : list(x))
    pos_ListArray = pos_rddArray.collect()
    min_Array = list(pos_ListArray)
    newRows = []
    nt = len(min_Array)
    nexs = percentageOver/100
    for i in range(nt):
        for j in range(nexs):
            neigh = random.randint(1,k)
            difs = min_Array[neigh][0] - min_Array[i][0]
            newRec = (min_Array[i][0]+random.random()*difs)
            newRows.insert(0,(newRec))
    newData_rdd = sc.parallelize(newRows)
    newData_rdd_new = newData_rdd.map(lambda x: Row(features = x, label = 1))
    new_data = newData_rdd_new.toDF()
    new_data_minor = dataInput_min.unionAll(new_data)
    new_data_major = dataInput_maj.sample(False, (float(percentageUnder)/float(100)))
    return new_data_major.unionAll(new_data_minor)

balanced_train_df = SmoteSampling(df_train)

In [0]:
balanced_train_df.write.parquet(f"{blob_url}/balanced_train_df")